##Inferencing

In [1]:
!huggingface-cli login



    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Token: Traceback (most recent call last):
  File "/usr/local/bin/huggingface-cli", line 8, in <module>
    sys.exit(main())
  File "/usr/local/lib/python3.10/dist-packages/huggingface_hub/commands/huggingface_cli.py", line 49, in main
  File "/usr/local/lib/python3.10/dist-packages/huggingface_hub/commands/user.py", line

In [2]:
# !pip install tensorflow[and-cuda]

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 417.9/417.9 MB 4.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 168.4/168.4 MB 6.8 MB/s eta 0:00:00
     ━━━━━╺━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 93.1/728.5 MB 92.2 MB/s eta 0:00:07ERROR: Operation cancelled by user
     ━━━━━╺━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 93.7/728.5 MB 90.9 MB/s eta 0:00:07


In [1]:
!pip install -q accelerate peft==0.4.0 bitsandbytes==0.40.2 transformers==4.31.0 trl==0.4.7

In [2]:
import os
import torch
from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    HfArgumentParser,
    TrainingArguments,
    pipeline,
    logging,
)
from peft import LoraConfig, PeftModel


device = 'cuda' if torch.cuda.is_available() else "cpu"
model = "deepapaikar/Llama_SCplusQA_10epochs"
tokenizer = AutoTokenizer.from_pretrained(model)
from transformers import AutoModelForCausalLM
model = AutoModelForCausalLM.from_pretrained(model, load_in_4bit=True)

Loading checkpoint shards:   0%|          | 0/3 [00:00<?, ?it/s]

Some weights of LlamaForCausalLM were not initialized from the model checkpoint at deepapaikar/Llama_SCplusQA_10epochs and are newly initialized: ['model.layers.9.self_attn.rotary_emb.inv_freq', 'model.layers.10.self_attn.rotary_emb.inv_freq', 'model.layers.24.self_attn.rotary_emb.inv_freq', 'model.layers.26.self_attn.rotary_emb.inv_freq', 'model.layers.29.self_attn.rotary_emb.inv_freq', 'model.layers.20.self_attn.rotary_emb.inv_freq', 'model.layers.5.self_attn.rotary_emb.inv_freq', 'model.layers.8.self_attn.rotary_emb.inv_freq', 'model.layers.23.self_attn.rotary_emb.inv_freq', 'model.layers.0.self_attn.rotary_emb.inv_freq', 'model.layers.16.self_attn.rotary_emb.inv_freq', 'model.layers.18.self_attn.rotary_emb.inv_freq', 'model.layers.12.self_attn.rotary_emb.inv_freq', 'model.layers.7.self_attn.rotary_emb.inv_freq', 'model.layers.2.self_attn.rotary_emb.inv_freq', 'model.layers.4.self_attn.rotary_emb.inv_freq', 'model.layers.31.self_attn.rotary_emb.inv_freq', 'model.layers.6.self_attn.r

### Mount file

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [3]:
import pandas as pd
df = pd.read_csv('/content/QA_test.csv')
df.head()

question  \
0  Which Yeshiva University school is Dr. Assa Co...   
1   What is Dr. Assa Cohen's primary research focus?   
2  Following his entry into Goldstein Golub Kessl...   
3  What educational background does Dr. Assa Cohe...   
4  In Dr. Patryk Perkowski's research at the Sy S...   

                                              answer  
0  Dr. Assa Cohen is joining the Sy Syms School o...  
1  Dr. Assa Cohen's research primarily focuses on...  
2  Steve Mayer became the managing partner of the...  
3  Dr. Assa Cohen has a Ph.D. in economics, and h...  
4  Dr. Patryk Perkowski's research primarily focu...

## Predictions

In [5]:
import gc
for i in range(10):
    torch.cuda.empty_cache()
    gc.collect()

In [7]:
# Run text generation pipeline with our next model
prompt = "Where is Yeshiva University? "
pipe = pipeline(task="text-generation", model=model, tokenizer=tokenizer, max_length=200)
result = pipe(f"<s>[INST] {prompt} [/INST]")
print(result[0]['generated_text'])

Xformers is not installed correctly. If you want to use memory_efficient_attention to accelerate training use the following command to install Xformers
pip install xformers.


<s>[INST] Where is Yeshiva University?  [/INST] New York City</s> Yeshiva University is a top 100 university in the United States.</s> It is located in New York and known for its business and technology programs.</s> It is also known for its central campus, which is in New York City.</s> The university is divided into five schools: Sackstein Center for Dispute Resolution, Stern College for Women, Sy Syms School of Business, Undergraduate Studies, and Wurzweiler School of Social Work.</s> Yeshiva University is a top 100 university in the United States, known for its business and technology programs, located in New York City, and divided into five schools.</s> The five schools include Belfer Center for Policy Studies, Cardozo School of Law, The Ferkauf Graduate School of Psychology, The George Washington University, and Yes


In [ ]:
# Assuming your DataFrame is named df
df['predicted'] = df.apply(lambda row: pipeline(
    task="text-generation", model=model, tokenizer=tokenizer, max_length=200)(
    f"<s>[INST] {row['question']} [/INST]"
)[0]['generated_text'], axis=1)

# Save the DataFrame to a new CSV file with the 'predicted' column
df.to_csv('/content/drive/MyDrive/Fall 2023/Model building/Llama/SC+QA Training/Dataset/Test Dataset/output_file.csv', index=False)

config.json:   0%|          | 0.00/685 [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/23.9k [00:00<?, ?B/s]

model-00001-of-00003.safetensors:   0%|          | 0.00/4.94G [00:00<?, ?B/s]

model-00002-of-00003.safetensors:   0%|          | 0.00/4.95G [00:00<?, ?B/s]

model-00003-of-00003.safetensors:   0%|          | 0.00/3.59G [00:00<?, ?B/s]

## Rogue

In [ ]:
!pip install rouge

In [ ]:
preds = pd.read_csv('/content/drive/MyDrive/Fall 2023/Model building/Llama/SC+QA Training/Dataset/Test Dataset/output_file.csv')

NameError: ignored

In [ ]:
preds

In [ ]:
from rouge import Rouge

In [ ]:
act_ans = []
pred_ans = []

for index, row in preds.iterrows():

  act_ans.append(row['answer'])
  pred_ans.append(row['predicted'])

In [ ]:
hyps, refs = map(list, (pred_ans,act_ans))
rouge = Rouge()

scores = rouge.get_scores(hyps, refs, avg=True)
scores

In [ ]:
from tabulate import tabulate

In [ ]:
# Create a list of dictionaries for tabulating the scores
score_table = [{'Metric': metric, 'Precision': score['p'], 'Recall': score['r'], 'F1-Score': score['f']} for metric, score in scores.items()]

# Print the scores in a tabular format
print(tabulate(score_table, headers='keys', tablefmt='grid'))